In [1]:
from mpl_toolkits.basemap import Basemap  # import Basemap matplotlib toolkit
import numpy as np
import matplotlib.pyplot as plt
import pygrib # import pygrib interface to grib_api
import pandas as pd
import os
import sys
import math
import folium
import csv 
import time

start = time.time()

%matplotlib inline

root = os.getcwd()
root_data = root + "/grib_data"
root_URL = "http://database.rish.kyoto-u.ac.jp/arch/jmadata/data/gpv/original/"

#timestomp like 201808010000 means that it is at 2019/04/09/08:00(UTC timezone)
year = "2019"
month = "04"
day = "18"
roottime="180000"


def getgrib(year,month,day,roottime):
    file_name = "Z__C_RJTD_"+str(year+month+day+roottime)+"_MSM_GPV_Rjp_Lsurf_FH00-15_grib2.bin"
    file_url = root_URL\
                +str(year + "/" + month + "/" + day +"/" )\
                +file_name
    root_file= "grib_data/"+file_name
    if os.path.isfile(root_file) == False:
            command = "wget -P grib_data/ "+ file_url
            os.system(command)

    getgrib_output = pygrib.open(root_file)
    return getgrib_output

def getrootgrib(year,month,day,time):
    file_name = "Z__C_RJTD_"+str(year+month+day+roottime)+"_MSM_GPV_Rjp_Lsurf_FH00-15_grib2.bin"    
    return "grib_data/"+file_name

In [2]:
print(os.path.isfile( getrootgrib(year,month,day,roottime) ))

True


In [3]:
grbs = getgrib(year,month,day,roottime)
latlons = grbs

In [4]:
print(os.path.isfile( getrootgrib(year,month,day,roottime) ))

True


In [5]:
#check parameters in gribfile
grb_1 = grbs.select(name='Pressure reduced to MSL')[0]

# lats,lonsは二次元配列で緯度経度が入っている
lats, lons = grb_1.latlons()

#一次元に変換
# 二次元のままでは描画できない
# 2次元の格子点を1次元配列にならす
flat_lats= np.ravel(lats)
flat_lons= np.ravel(lons)

pd_rad= {'lons':flat_lons, 'lats':flat_lats}
pd_Uwind= {'lons':flat_lons, 'lats':flat_lats}
pd_Vwind= {'lons':flat_lons, 'lats':flat_lats}
pd_temp= {'lons':flat_lons, 'lats':flat_lats}

i,j,k,l =0,0,0,0

for grb in grbs:
    print(grb)
    
    if grb.name == "Downward short-wave radiation flux":
        radiation = grb.values
        flat_radiation = np.ravel(radiation)
        pd_name="radiation FH"+str(i)+"-"+str(i+1)+"W/m2(avg)"
        pd_rad[pd_name]=flat_radiation
        i=i+1

    elif grb.name == "10 metre U wind component":
        Uwind = grb.values
        flat_Uwind = np.ravel(Uwind)
        pd_name="Uwind FH"+str(j)+"m/s"
        pd_Uwind[pd_name]=flat_Uwind
        j=j+1

    elif grb.name == "10 metre V wind component":
        Vwind = grb.values
        flat_Vwind = np.ravel(Vwind)
        pd_name="Vwind FH"+str(k)+"m/s"
        pd_Uwind[pd_name]=flat_Uwind
        k=k+1

    elif grb.name == "Temperature":
        temperature = grb.values
        #華氏を摂氏に変換
        flat_temperature= np.ravel(temperature)
        flat_temperature=flat_temperature-273.115
        pd_name="temperature FH"+str(l)
        pd_temp[pd_name]=flat_temperature
        l=l+1

1:Pressure reduced to MSL:Pa (instant):regular_ll:meanSea:level 0:fcst time 0 hrs:from 201904181800
2:Surface pressure:Pa (instant):regular_ll:surface:level 0:fcst time 0 hrs:from 201904181800
3:10 metre U wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 10 m:fcst time 0 hrs:from 201904181800
4:10 metre V wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 10 m:fcst time 0 hrs:from 201904181800
5:Temperature:K (instant):regular_ll:heightAboveGround:level 1.5 m:fcst time 0 hrs:from 201904181800
6:Relative humidity:% (instant):regular_ll:heightAboveGround:level 1.5 m:fcst time 0 hrs:from 201904181800
7:Low cloud cover:% (instant):regular_ll:surface:level 0:fcst time 0 hrs:from 201904181800
8:Medium cloud cover:% (instant):regular_ll:surface:level 0:fcst time 0 hrs:from 201904181800
9:High cloud cover:% (instant):regular_ll:surface:level 0:fcst time 0 hrs:from 201904181800
10:Total cloud cover:% (instant):regular_ll:surface:level 0:fcst time 0 hrs:from 2

117:Total precipitation:kg m-2 (accum):regular_ll:surface:level 0:fcst time 8-9 hrs (accum):from 201904181800
118:Downward short-wave radiation flux:W m**-2 (avg):regular_ll:surface:level 0:fcst time 8-9 hrs (avg):from 201904181800
119:Pressure reduced to MSL:Pa (instant):regular_ll:meanSea:level 0:fcst time 10 hrs:from 201904181800
120:Surface pressure:Pa (instant):regular_ll:surface:level 0:fcst time 10 hrs:from 201904181800
121:10 metre U wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 10 m:fcst time 10 hrs:from 201904181800
122:10 metre V wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 10 m:fcst time 10 hrs:from 201904181800
123:Temperature:K (instant):regular_ll:heightAboveGround:level 1.5 m:fcst time 10 hrs:from 201904181800
124:Relative humidity:% (instant):regular_ll:heightAboveGround:level 1.5 m:fcst time 10 hrs:from 201904181800
125:Low cloud cover:% (instant):regular_ll:surface:level 0:fcst time 10 hrs:from 201904181800
126:Medium clou

In [6]:
#緯度経度の範囲を選択
east_lon=131.69
west_lon=129.4337
north_lat=34.1413
south_lat=31.01

In [7]:
#range adjust
def range_ajust(east_lon,west_lon,north_lat,south_lat,df_all):
    df=df_all[df_all['lons'] > west_lon]
    df=df[df['lons'] < east_lon]

    df=df[df['lats'] > south_lat]
    df=df[df['lats'] < north_lat]
    return df



## Select parameter temperature, Uwind, Vwind, radiation

In [8]:
########################
df_para = "temperature"
########################

if df_para == "temperature":
    df_input=pd.DataFrame(pd_temp)

elif df_para == "Uwind":
    df_input=pd.DataFrame(pd_Uwind)
   
elif df_para == "Vwind":
    df_input=pd.DataFrame(pd_Vwind)
    
elif df_para == "radiation":
    df_input=pd.DataFrame(pd_rad)
    


df = range_ajust(east_lon,west_lon,north_lat,south_lat,df_input)
map_lat=df['lats'].values
map_lon=df['lons'].values
df = np.round(df,2)
print(len(df))
df[:10]

2294


lons  lats  temperature FH0  temperature FH1  temperature FH2  \
130021  129.44  34.1            17.23            17.20            16.85   
130022  129.50  34.1            17.24            17.22            16.94   
130023  129.56  34.1            17.23            17.22            16.99   
130024  129.62  34.1            17.19            17.19            17.02   
130025  129.69  34.1            17.16            17.16            17.04   
130026  129.75  34.1            17.12            17.13            17.04   
130027  129.81  34.1            17.07            17.09            17.04   
130028  129.88  34.1            17.02            17.06            17.04   
130029  129.94  34.1            16.96            17.03            17.02   
130030  130.00  34.1            16.93            17.00            17.02   

        temperature FH3  temperature FH4  temperature FH5  temperature FH6  \
130021            16.21            15.86            15.90            16.18   
130022            16.36            16.03            15.94            16.18   
130023            16.47            16.15            15.99            16.19   
130024            16.55            16.25            16.02            16.22   
130025            16.60            16.30            16.05            16.27   
130026            16.64            16.36            16.07            16.32   
130027            16.68            16.40            16.10            16.35   
130028            16.71            16.45            16.12            16.38   
130029            16.74            16.48            16.15            16.40   
130030            16.78            16.53            16.19            16.41   

        temperature FH7  temperature FH8  temperature FH9  temperature FH10  \
130021            16.35            16.17            16.07             15.93   
130022            16.35            16.15            16.06             15.91   
130023            16.33            16.14            16.03             15.88   
130024            16.32            16.10            15.98             15.85   
130025            16.30            16.09            15.95             15.82   
130026            16.30            16.07            15.93             15.82   
130027            16.32            16.06            15.90             15.82   
130028            16.33            16.06            15.90             15.84   
130029            16.35            16.07            15.88             15.85   
130030            16.38            16.09            15.90             15.87   

        temperature FH11  temperature FH12  temperature FH13  \
130021             15.69             15.04             14.83   
130022             15.74             15.12             14.85   
130023             15.74             15.16             14.89   
130024             15.72             15.18             14.92   
130025             15.69             15.18             14.94   
130026             15.68             15.18             14.94   
130027             15.65             15.18             14.92   
130028             15.63             15.18             14.91   
130029             15.62             15.19             14.89   
130030             15.60             15.21             14.89   

        temperature FH14  temperature FH15  
130021             14.79             14.67  
130022             14.81             14.67  
130023             14.79             14.64  
130024             14.76             14.61  
130025             14.75             14.58  
130026             14.71             14.55  
130027             14.68             14.53  
130028             14.65             14.52  
130029             14.64             14.50  
130030             14.64             14.50

In [9]:
FH0=df.iloc[:,2].values
FH1=df.iloc[:,3].values
FH2=df.iloc[:,4].values
FH3=df.iloc[:,5].values
FH4=df.iloc[:,6].values
FH5=df.iloc[:,7].values

In [10]:
from folium import plugins

#lat-long of focus area and zoom start
map = folium.Map([33.518022,130.471583], zoom_start=12)

# Mapbox makes some nice map tiles,
# Stamen also produce some cool map tiles which typically work at all zoom levels.
tile = folium.TileLayer('Stamen Terrain').add_to(map)

#adding marker and popup of temperature
for i in range(0,len(map_lat)):
    
    icon_number = plugins.BeautifyIcon(
    border_color='#00ABDC',
    text_color='#00ABDC',
    border_width=2,
    number=str(int(FH0[i])),
    inner_icon_style='margin-top:0;')
    
    folium.Marker(location=[float(map_lat[i])  ,float(map_lon[i])],\
                  popup="___"+df_para+"___"+"\n"\
                          +"__lat= "+str(map_lat[i])+"__\n"\
                          +"__lon= "+str(map_lon[i])+"__\n"\
                          +"__FH0= "+str(FH0[i])+"__\n"\
                          +"__FH1 = "+str(FH1[i])+"__\n"\
                          +"__FH2 = "+str(FH2[i])+"__\n"\
                          +"__FH3 = "+str(FH3[i])+"__\n"\
                          +"__FH4 = "+str(FH4[i])+"__\n"\
                          +"__FH5 = "+str(FH5[i])+"__\n",\
                 icon=icon_number).add_to(map)
    
#we can change tiles with help of LayerConrol
folium.LayerControl().add_to(map)

#Adding mouse position
formatter = "function(num) {return L.Util.formatNum(num, 3) + ' º ';};"

folium.plugins.MousePosition(
    position='topright',
    separator=' | ',
    empty_string='NaN',
    lng_first=True,
    num_digits=20,
    prefix='Coordinates:',
    lat_formatter=formatter,
    lng_formatter=formatter
).add_to(map)

map_name="Output_MAP/"+"FH_"+df_para+"_Map_" + year + "_" + month + "_" + day+ "_" + roottime+".html"
csv_name="Output_CSV/"+"FH_"+df_para + year + "_" + month + "_" + day+ "_" + roottime+".csv"

df.to_csv(csv_name, encoding='utf-8', index=False)
map.save(outfile=map_name)

map

In [11]:
elapsed_time = time.time() - start

print("elapsed_time:{0}".format(elapsed_time))

elapsed_time:14.300963401794434
